# RSI 70-30 example

- This is a backtest example notebook
- A signal-based algorithmic trading strategy for two pairs: BTC-USD and ETH-USD
- An example strategy [for RSI rebalance](https://help.tokensets.com/en/articles/3541009-eth-btc-rsi-ratio-trading-set-details)
- We backtest using Binance data 2020-2024

# Set up

Set up Trading Strategy data client.


In [7]:
import numpy as np

from tradingstrategy.client import Client

client = Client.create_jupyter_client()

Started Trading Strategy in Jupyter notebook environment, configuration is stored in /Users/moo/.tradingstrategy


# Load data

We use Binance data so we get a longer period of data.

In [8]:
import datetime
from tradingstrategy.timebucket import TimeBucket
from tradeexecutor.utils.binance import create_binance_universe

strategy_universe = create_binance_universe(
    ["BTCUSDT", "ETHUSDT"],   # Binance internal tickers later mapped to Trading strategy DEXPair metadata class
    candle_time_bucket=TimeBucket.d1,
    stop_loss_time_bucket=TimeBucket.h4,
    start_at=datetime.datetime(2020, 1, 1),
    end_at=datetime.datetime(2024, 1, 1),
    include_lending=False
)


  0%|          | 0/2 [00:00<?, ?it/s]

# Show loaded trading universe

Display generic troubleshooting information about the loaded data.

In [9]:
pairs = strategy_universe.data_universe.pairs  # Trading pairs metadata
candles = strategy_universe.data_universe.candles  # Candles for all trading pairs

print(f"Loaded {candles.get_candle_count():,} candles.")

for pair in pairs.iterate_pairs():
    pair_candles = candles.get_candles_by_pair(pair)
    first_close = pair_candles.iloc[0]["close"]
    first_close_at = pair_candles.index[0]
    print(f"Pair {pair} first close price {first_close} at {first_close_at}")
    display(pair_candles)

Loaded 17,542 candles.
Pair <Pair #1 BTC - USDT at exchange binance> first close price 7225.01 at 2020-01-01 00:00:00


open      high       low     close       volume  \
timestamp                                                                  
2020-01-01 00:00:00   7195.24   7245.00   7175.46   7225.01  2833.749180   
2020-01-01 04:00:00   7225.00   7236.27   7199.11   7209.83  2061.295051   
2020-01-01 08:00:00   7209.83   7237.73   7180.00   7197.20  3166.654361   
2020-01-01 12:00:00   7197.20   7255.00   7196.15   7234.19  3492.537459   
2020-01-01 16:00:00   7234.20   7249.99   7214.00   7229.48  2980.583291   
...                       ...       ...       ...       ...          ...   
2024-01-01 04:00:00  42330.50  42500.00  42180.77  42492.46  2706.998800   
2024-01-01 08:00:00  42492.46  42762.39  42452.58  42690.20  2948.802740   
2024-01-01 12:00:00  42690.21  42847.07  42580.00  42783.05  2936.444060   
2024-01-01 16:00:00  42783.05  43550.00  42664.42  43517.99  5686.971640   
2024-01-01 20:00:00  43517.98  44184.10  43361.60  44179.55  8946.998440   

                     pair_id base_token_symbol quote_token_symbol  \
timestamp                                                           
2020-01-01 00:00:00        1               BTC               USDT   
2020-01-01 04:00:00        1               BTC               USDT   
2020-01-01 08:00:00        1               BTC               USDT   
2020-01-01 12:00:00        1               BTC               USDT   
2020-01-01 16:00:00        1               BTC               USDT   
...                      ...               ...                ...   
2024-01-01 04:00:00        1               BTC               USDT   
2024-01-01 08:00:00        1               BTC               USDT   
2024-01-01 12:00:00        1               BTC               USDT   
2024-01-01 16:00:00        1               BTC               USDT   
2024-01-01 20:00:00        1               BTC               USDT   

                    exchange_slug  chain_id  ...  buy_volume_all_time  \
timestamp                                    ...                        
2020-01-01 00:00:00       binance      -1.0  ...                  0.0   
2020-01-01 04:00:00       binance      -1.0  ...                  0.0   
2020-01-01 08:00:00       binance      -1.0  ...                  0.0   
2020-01-01 12:00:00       binance      -1.0  ...                  0.0   
2020-01-01 16:00:00       binance      -1.0  ...                  0.0   
...                           ...       ...  ...                  ...   
2024-01-01 04:00:00       binance      -1.0  ...                  0.0   
2024-01-01 08:00:00       binance      -1.0  ...                  0.0   
2024-01-01 12:00:00       binance      -1.0  ...                  0.0   
2024-01-01 16:00:00       binance      -1.0  ...                  0.0   
2024-01-01 20:00:00       binance      -1.0  ...                  0.0   

                                                        address  exchange_id  \
timestamp                                                                      
2020-01-01 00:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   
2020-01-01 04:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   
2020-01-01 08:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   
2020-01-01 12:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   
2020-01-01 16:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   
...                                                         ...          ...   
2024-01-01 04:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   
2024-01-01 08:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   
2024-01-01 12:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   
2024-01-01 16:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   
2024-01-01 20:00:00  0x1d06ef1d6470d25f8e3d6f04f5acc111f176939c  129875571.0   

                                                 token0_address  \
timestamp                                                         
2020-01-01 00

Pair <Pair #2 ETH - USDT at exchange binance> first close price 130.2 at 2020-01-01 00:00:00


open     high      low    close       volume  pair_id  \
timestamp                                                                       
2020-01-01 00:00:00   129.16   130.98   128.68   130.20  31685.73908        2   
2020-01-01 04:00:00   130.21   130.75   130.11   130.24  15457.58966        2   
2020-01-01 08:00:00   130.24   131.87   129.87   130.74  27822.94195        2   
2020-01-01 12:00:00   130.74   132.40   130.70   132.08  24010.28657        2   
2020-01-01 16:00:00   132.08   133.05   131.57   131.86  20158.22421        2   
...                      ...      ...      ...      ...          ...      ...   
2024-01-01 04:00:00  2273.80  2287.88  2265.24  2284.67  28107.51330        2   
2024-01-01 08:00:00  2284.68  2305.05  2280.00  2304.47  27894.10920        2   
2024-01-01 12:00:00  2304.47  2318.34  2294.84  2314.70  32165.85220        2   
2024-01-01 16:00:00  2314.69  2340.98  2306.48  2337.26  46802.25260        2   
2024-01-01 20:00:00  2337.27  2352.37  2323.66  2352.04  45993.63050        2   

                    base_token_symbol quote_token_symbol exchange_slug  \
timestamp                                                                
2020-01-01 00:00:00               ETH               USDT       binance   
2020-01-01 04:00:00               ETH               USDT       binance   
2020-01-01 08:00:00               ETH               USDT       binance   
2020-01-01 12:00:00               ETH               USDT       binance   
2020-01-01 16:00:00               ETH               USDT       binance   
...                               ...                ...           ...   
2024-01-01 04:00:00               ETH               USDT       binance   
2024-01-01 08:00:00               ETH               USDT       binance   
2024-01-01 12:00:00               ETH               USDT       binance   
2024-01-01 16:00:00               ETH               USDT       binance   
2024-01-01 20:00:00               ETH               USDT       binance   

                     chain_id  ...  buy_volume_all_time  \
timestamp                      ...                        
2020-01-01 00:00:00      -1.0  ...                  0.0   
2020-01-01 04:00:00      -1.0  ...                  0.0   
2020-01-01 08:00:00      -1.0  ...                  0.0   
2020-01-01 12:00:00      -1.0  ...                  0.0   
2020-01-01 16:00:00      -1.0  ...                  0.0   
...                       ...  ...                  ...   
2024-01-01 04:00:00      -1.0  ...                  0.0   
2024-01-01 08:00:00      -1.0  ...                  0.0   
2024-01-01 12:00:00      -1.0  ...                  0.0   
2024-01-01 16:00:00      -1.0  ...                  0.0   
2024-01-01 20:00:00      -1.0  ...                  0.0   

                                                        address  exchange_id  \
timestamp                                                                      
2020-01-01 00:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   
2020-01-01 04:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   
2020-01-01 08:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   
2020-01-01 12:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   
2020-01-01 16:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   
...                                                         ...          ...   
2024-01-01 04:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   
2024-01-01 08:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   
2024-01-01 12:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   
2024-01-01 16:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   
2024-01-01 20:00:00  0xe82ac67166a910f4092c23f781cd39e46582ec9c  129875571.0   

                                                 token0_address  \
timestamp                                                         
2020-01-01 00:00:00  0x4b2d72c1cb89c0b2b320c43bb67ff79f562f5ff4 

# Trading algorithm

In [10]:
from tradingstrategy.chain import ChainId
from typing import List, Dict

from pandas_ta.momentum import rsi
import pandas as pd

from tradeexecutor.strategy.trading_strategy_universe import TradingStrategyUniverse
from tradeexecutor.state.visualisation import PlotKind, PlotShape
from tradeexecutor.state.trade import TradeExecution
from tradeexecutor.strategy.pricing_model import PricingModel
from tradeexecutor.state.state import State

# List of pair descriptions we used to look up pair metadata
our_pairs = [
    (ChainId.centralised_exchange, "binance", "BTC", "USDT"),
    (ChainId.centralised_exchange, "binance", "ETH", "USDT"),
]

rsi_high = 70  # RSI trigger threshold for decision making
rsi_low = 30  # RSI trigger threshold for decision making

lookback_candles = 120


def decide_trades(
        timestamp: pd.Timestamp,
        strategy_universe: TradingStrategyUniverse,
        state: State,
        pricing_model: PricingModel,
        cycle_debug_data: Dict) -> List[TradeExecution]:

    trades = []  # This is the list of trades we are going to  make in  this cycle
    cash = state.portfolio.get_current_cash()  # How much cash we have in a hand

    visualisation = state.visualisation  # Helper class to visualise strategy output
    current_rsi_values = {}
    current_price = {}

    # Resolve our pair metadata for our two pair strategy
    btc_pair = pairs.get_pair_by_human_description(our_pairs[0])
    eth_pair = pairs.get_pair_by_human_description(our_pairs[1])

    #
    # Indicators
    #
    # Calculate indicators for each pair.
    #

    for pair in [btc_pair, eth_pair]:

        pair_candles = candles.get_last_entries_by_pair_and_timestamp(pair, timestamp)
        assert pair_candles is not None
        rsi_series = rsi(pair_candles["close"], length=14)  # Will return None if the data buffer does not have enough days to look back

        # Reset indicators for this cycle and this pair
        current_rsi_values[pair] = None
        current_price[pair] = None

        if len(pair_candles) > 0:
            # We have enough data to get the latest price
            current_price[pair] = pair_candles["close"][-1]

        if rsi_series is not None:
            current_val = rsi_series[-1]
            if np.isfinite(current_val):
                # We have enough data and good value for RSI
                assert 0 < current_val < 100, f"RSI sanity check failed: {pair}: {current_val}"  # Check we are in expected range
                current_rsi_values[pair] = current_val

    #
    # Visualisations
    #

    visualisation.plot_indicator(
        timestamp,
        f"ETH price",
        PlotKind.technical_indicator_detached,
        current_price[eth_pair],
        colour="green",
    )

    # Draw ETH/BTC price as a separate indicator
    if current_price[btc_pair] and current_price[eth_pair]:
        visualisation.plot_indicator(
            timestamp,
            f"ETH/BTC price",
            PlotKind.technical_indicator_detached,
            current_price[eth_pair] / current_price[btc_pair],
            colour="green",
        )

    # Draw RSI between its trigger zones for this pair of we got a valid value for RSI for this pair
    for pair in[btc_pair, eth_pair]:

        if current_rsi_values[pair]:

            token = pair.base_token_symbol  # "ETH" or "BTC"

            # Current daily
            visualisation.plot_indicator(
                timestamp,
                f"RSI {token}",
                PlotKind.technical_indicator_detached,
                current_rsi_values[pair],
                colour="green",
            )

            # Low (vertical line)
            visualisation.plot_indicator(
                timestamp,
                f"RSI {token} low trigger",
                PlotKind.technical_indicator_overlay_on_detached,
                rsi_low,
                detached_overlay_name=f"RSI {token}",
                plot_shape=PlotShape.horizontal_vertical,
                colour="red",
            )

            # High (vertical line)
            visualisation.plot_indicator(
                timestamp,
                f"RSI {token} high trigger",
                PlotKind.technical_indicator_overlay_on_detached,
                rsi_high,
                detached_overlay_name=f"RSI {token}",
                plot_shape=PlotShape.horizontal_vertical,
                colour="red",
            )


    return trades

# Backtest

In [11]:
from tradeexecutor.strategy.cycle import CycleDuration

from tradeexecutor.backtest.backtest_runner import run_backtest_inline

state, universe, debug_dump = run_backtest_inline(
    name="RSI multipair",
    engine_version="0.3",
    decide_trades=decide_trades,
    client=client,
    cycle_duration=CycleDuration.cycle_1d,
    universe=strategy_universe,
    initial_deposit=10_000,
)

trade_count = len(list(state.portfolio.get_all_trades()))
print(f"Backtesting completed, backtested strategy made {trade_count} trades")

  0%|          | 0/126302400 [00:00<?, ?it/s]

Backtesting completed, backtested strategy made 0 trades


In [12]:
from tradeexecutor.visual.single_pair import visualise_single_pair
from tradingstrategy.charting.candle_chart import VolumeBarMode

# Use BTC pair as the primary price source
# Get BTC pair
btc_pair = pairs.get_pair_by_human_description(our_pairs[0])

figure = visualise_single_pair(
    state,
    strategy_universe.data_universe.candles,
    pair_id=btc_pair.pair_id,
    volume_bar_mode=VolumeBarMode.hidden,
    height = 1000,
)

figure.show()